In [1]:
import pandas as pd
import re
import glob
import ipywidgets
from ipyleaflet import Map, basemaps, AntPath, GeoJSON
from ipywidgets import widgets as w
import json

In [2]:
!ls "/mapr/datalake.test.act.gov.au/Data/TCCS/TrafficData/SourceData/"

2020-05-29_traffic.csv	2020-06-18_traffic.csv	2020-07-09_traffic.csv
2020-06-01_traffic.csv	2020-06-19_traffic.csv	2020-07-10_traffic.csv
2020-06-02_traffic.csv	2020-06-22_traffic.csv	2020-07-13_traffic.csv
2020-06-03_traffic.csv	2020-06-23_traffic.csv	2020-07-14_traffic.csv
2020-06-04_traffic.csv	2020-06-24_traffic.csv	2020-07-15_traffic.csv
2020-06-05_traffic.csv	2020-06-25_traffic.csv	2020-07-16_traffic.csv
2020-06-08_traffic.csv	2020-06-26_traffic.csv	2020-07-17_traffic.csv
2020-06-09_traffic.csv	2020-07-01_traffic.csv	2020-07-20_traffic.csv
2020-06-10_traffic.csv	2020-07-02_traffic.csv	2020-07-21_traffic.csv
2020-06-11_traffic.csv	2020-07-03_traffic.csv	map.geojson
2020-06-12_traffic.csv	2020-07-06_traffic.csv	response.json
2020-06-15_traffic.csv	2020-07-07_traffic.csv	traffic.csv
2020-06-16_traffic.csv	2020-07-08_traffic.csv


In [3]:
with open('/mapr/datalake.test.act.gov.au/Data/TCCS/TrafficData/SourceData/map.geojson') as f:
    geo_json = json.load(f)


In [4]:
def reverse(list):
    mutatedList = []
    for i in list:
        i.reverse()
        mutatedList.append(i)
    list=mutatedList[:]
    return mutatedList

In [5]:
co_ordinates = geo_json['features'][0]['geometry']['coordinates']
co_ordinates_r = reverse(co_ordinates)
print(co_ordinates_r)

[[-35.28948774935104, 149.11897659301758], [-35.28815662215793, 149.119234085083], [-35.2868254730776, 149.12060737609863], [-35.28626498270641, 149.1229248046875], [-35.286615289643116, 149.12489891052246], [-35.28787638206515, 149.1261005401611], [-35.28948774935104, 149.1262722015381], [-35.29074879702827, 149.1262722015381], [-35.291519427604776, 149.126615524292], [-35.28990810075949, 149.12670135498047], [-35.28612485950733, 149.12755966186523], [-35.28570448845503, 149.1293621063232], [-35.286755411993404, 149.13288116455078], [-35.286755411993404, 149.13442611694336], [-35.2873158989694, 149.13519859313965], [-35.28787638206515, 149.13579940795898], [-35.28962786672971, 149.13983345031738], [-35.28997815911536, 149.14034843444824], [-35.28654522837703, 149.14318084716794], [-35.2827618299769, 149.13777351379395], [-35.281500657891186, 149.13897514343262], [-35.275614928447574, 149.1352844238281], [-35.27596528145866, 149.13339614868164], [-35.270709827167735, 149.13451194763184

In [6]:
geo_json['features'][0]['geometry']['coordinates']=co_ordinates_r

In [7]:
geo_json['features'][0]['geometry']['coordinates']

[[-35.28948774935104, 149.11897659301758],
 [-35.28815662215793, 149.119234085083],
 [-35.2868254730776, 149.12060737609863],
 [-35.28626498270641, 149.1229248046875],
 [-35.286615289643116, 149.12489891052246],
 [-35.28787638206515, 149.1261005401611],
 [-35.28948774935104, 149.1262722015381],
 [-35.29074879702827, 149.1262722015381],
 [-35.291519427604776, 149.126615524292],
 [-35.28990810075949, 149.12670135498047],
 [-35.28612485950733, 149.12755966186523],
 [-35.28570448845503, 149.1293621063232],
 [-35.286755411993404, 149.13288116455078],
 [-35.286755411993404, 149.13442611694336],
 [-35.2873158989694, 149.13519859313965],
 [-35.28787638206515, 149.13579940795898],
 [-35.28962786672971, 149.13983345031738],
 [-35.28997815911536, 149.14034843444824],
 [-35.28654522837703, 149.14318084716794],
 [-35.2827618299769, 149.13777351379395],
 [-35.281500657891186, 149.13897514343262],
 [-35.275614928447574, 149.1352844238281],
 [-35.27596528145866, 149.13339614868164],
 [-35.270709827167

In [8]:
geo_json_cra_layer = GeoJSON(data1=geo_json,
                                 style = {'color': 'blue', 
                                          'opacity': 1.0, 
                                          'weight': 1.9,
                                          'fill': 'green',
                                          'fillOpacity': 0.5})

In [9]:
def changelatlon(coordinates):
    coordinate_list=[]
    loc=re.findall("[[][-]|[0-9]+[.][0-9]+[,]\s[-][0-9]+[.][0-9]+[]]", coordinates)
    for i in range(0,len(loc)):
        longitude_loc=re.search("[-]|[0-9]+[.][0-9]+", loc[i])
        longitude_span= longitude_loc.span()
        longitude=float(loc[i][longitude_span[0]:longitude_span[1]])
        latitude=float(loc[i][longitude_span[1]+2:-1])
        new_cordinates=[latitude,longitude]
        coordinate_list.append(new_cordinates)

    return coordinate_list

In [10]:
def plot_coordinates(date):
    c = visuald.loc[visuald["Timestamp"]==date]
    for i,r in c.iterrows():
        if int(r.loc["Delay(s)"]) > 20:
            traffic_red = AntPath(title=r.loc["Name"],locations=changelatlon(r.loc["LineCoOrdinates"]),dash_array=[1, 10],delay=int(r.loc["Delay(s)"])*100,color='red',pulse_color='#3f6fba')
            m.add_layer(traffic_red)
        elif int(r.loc["Delay(s)"]) < 3 & int(r.loc["Delay(s)"])> 1:
            traffic_green = AntPath(locations=changelatlon(r.loc["LineCoOrdinates"]),dash_array=[1, 10],delay=int(r.loc["Delay(s)"])*10,color='green',pulse_color='#3f6fba')
            m.add_layer(traffic_green)
        #elif int(r.loc["Delay(s)"]) < 50 & int(r.loc["Delay(s)"])> 10:
            #traffic_blue = AntPath(locations=changelatlon(r.loc["LineCoOrdinates"]),dash_array=[1, 10],delay=int(r.loc["Delay(s)"])*10,color='blue',pulse_color='#3f6fba')
            #m.add_layer(traffic_blue)


In [11]:
def readcsvs(path):
    file_format = "[0-9]*[_traffic.csv]"
    col_header = ['Id','Name','Timestamp','OriginSiteId','DestSiteId','MinTimeTaken(s)','TimeTaken(s)',
                  'Delay(s)','ExcessDelay','Speed','Congestion','Length(m)','Direction','LineCoOrdinates']
    df = pd.DataFrame(columns=col_header)

    for file in glob.glob(path+file_format):
        try:
            df_file = pd.read_csv(file,usecols = col_header)
            df = df.append(df_file)
        except:
            print('error in file : ',file)

    print('number of files processed :', len(glob.glob(path+file_format)))
    total_before_drop = len(df) 
    #delete rows where headers are repeated
    drop_index_list = df[df.Id == "Id"].index.values.astype(int) #drop all rows which has entry as "Id" in "id' Column
    df = df.drop(index = drop_index_list)
    print('length of df', len(df))
    total_after_drop = len(df) 
    num_rows_dropped = total_before_drop - total_after_drop
    #sort by timestamp
    df['Timestamp']= pd.to_datetime(df['Timestamp'],format = "%Y-%m-%dT%H:%M:%S%z")  
    df = df.sort_values(by=['Timestamp'])
    df.info()
    df.head
    #initial_value = df.loc[0,'Timestamp']
    initial_value = df['Timestamp'].iloc[0]
    print('initial_value : ',initial_value)
    return df, initial_value

In [12]:
datapath="/mapr/datalake.test.act.gov.au/Data/TCCS/TrafficData/SourceData/"
data , initial_value = readcsvs(datapath)

number of files processed : 35
length of df 99839
<class 'pandas.core.frame.DataFrame'>
Int64Index: 99839 entries, 283 to 1527
Data columns (total 14 columns):
 #   Column           Non-Null Count  Dtype                                
---  ------           --------------  -----                                
 0   Id               99839 non-null  object                               
 1   Name             99839 non-null  object                               
 2   Timestamp        99839 non-null  datetime64[ns, pytz.FixedOffset(600)]
 3   OriginSiteId     99839 non-null  object                               
 4   DestSiteId       99839 non-null  object                               
 5   MinTimeTaken(s)  99839 non-null  object                               
 6   TimeTaken(s)     99839 non-null  object                               
 7   Delay(s)         99839 non-null  object                               
 8   ExcessDelay      99839 non-null  object                               
 9  

In [13]:
cra_bounds=[22,26,27,28,29,30,32,34,73,75,77,85,88,94,114,116,118,120,226,234,236,240,289,295,326,328,331,333,337,370,372,375]

In [14]:
def plot_id(date):
    c = visuald.loc[visuald["Timestamp"]==date]
    for i,r in c.iterrows():
        if int(r.loc["Id"])in cra_bounds:
            if int(r.loc["Delay(s)"]) > 50:
                traffic_red = AntPath(title=r.loc["Name"],locations=changelatlon(r.loc["LineCoOrdinates"]),dash_array=[1, 10],delay=1000,color='red',pulse_color='#3f6fba')
                m.add_layer(traffic_red)
            elif int(r.loc["Delay(s)"]) < 10 & int(r.loc["Delay(s)"])>= 1:
                traffic_green = AntPath(locations=changelatlon(r.loc["LineCoOrdinates"]),dash_array=[1, 10],delay=1000,color='green',pulse_color='#3f6fba')
                m.add_layer(traffic_green)
    #m.add_layer(geo_json_cra_layer)
    return
        #elif int(r.loc["Delay(s)"]) < 3 & int(r.loc["Delay(s)"])> 1:
        #    traffic_green = AntPath(locations=changelatlon(r.loc["LineCoOrdinates"]),dash_array=[1, 10],delay=int(r.loc["Delay(s)"])*10,color='green',pulse_color='#3f6fba')
        #    m.add_layer(traffic_green)
        #elif int(r.loc["Delay(s)"]) < 50 & int(r.loc["Delay(s)"])> 10:
            #traffic_blue = AntPath(locations=changelatlon(r.loc["LineCoOrdinates"]),dash_array=[1, 10],delay=int(r.loc["Delay(s)"])*10,color='blue',pulse_color='#3f6fba')
            #m.add_layer(traffic_blue)

In [15]:

visuald= data[["Timestamp","LineCoOrdinates","Delay(s)","Name", "Id"]]
#selection_slider=ipywidgets.SelectionSlider(options= list(visuald["Timestamp"]), value="2020-06-03T8:59:30+10:00", description="Slider", disabled=False, continuous_update=False,orientation='horizontal',readout=True)
selection_slider=ipywidgets.SelectionSlider(options= list(visuald["Timestamp"]), value=initial_value, description="Slider", disabled=False, continuous_update=False,orientation='horizontal',readout=True)
m = Map(center=[-35.2749989,149.1333328], zoom=13,scroll_wheel_zoom=True,  # Allow zoom with the mouse scroll wheel
    layout=w.Layout(
        width='800px',   # Set Width of the map to 600 pixels, examples: "100%", "5em", "300px"
        height='600px',  # Set height of the map
    ))

display(m)

ipywidgets.interact(plot_id, date=selection_slider)

Map(center=[-35.2749989, 149.1333328], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_tit…

interactive(children=(SelectionSlider(continuous_update=False, description='Slider', options=(Timestamp('2020-…

<function __main__.plot_id(date)>

In [ ]:

play = ipywidgets.Play(
    value=50,
    step=1,
    interval=500,
    description="Press play",
    disabled=False
)
#slider = ipywidgets.IntSlider()
slider=selection_slider
ipywidgets.link((play, 'value'), (slider, 'value'))
ipywidgets.HBox([play, slider])